<a href="https://colab.research.google.com/github/abishekchiff/capstone-files-/blob/master/VQA1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
!pip install tensorflow==2.0.0-alpha0 


     |████████████████████████████████| 79.9MB 1.2MB/s 
     |████████████████████████████████| 61kB 22.7MB/s 
     |████████████████████████████████| 3.0MB 39.6MB/s 
     |████████████████████████████████| 419kB 47.1MB/s 
  Found existing installation: tensorflow 1.13.1
    Uninstalling tensorflow-1.13.1:
      Successfully uninstalled tensorflow-1.13.1


In [0]:
from google.colab import drive
drive.mount('/content/gdrive')

In [0]:
import tensorflow as tf

In [0]:
import time

In [0]:

tf.__version__

'2.0.0-alpha0'

In [0]:
!mkdir train test val

In [0]:
!wget http://images.cocodataset.org/zips/train2014.zip train

--2019-06-09 19:54:07--  http://images.cocodataset.org/zips/train2014.zip
Resolving images.cocodataset.org (images.cocodataset.org)... 52.216.88.67
Connecting to images.cocodataset.org (images.cocodataset.org)|52.216.88.67|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 13510573713 (13G) [application/zip]
Saving to: ‘train2014.zip’

train2014.zip       100%[===================>]  12.58G  36.1MB/s    in 6m 0s   

2019-06-09 20:00:07 (35.7 MB/s) - ‘train2014.zip’ saved [13510573713/13510573713]

--2019-06-09 20:00:07--  http://train/
Resolving train (train)... failed: Name or service not known.
wget: unable to resolve host address ‘train’
FINISHED --2019-06-09 20:00:07--
Total wall clock time: 6m 1s
Downloaded: 1 files, 13G in 6m 0s (35.7 MB/s)


In [0]:
!unzip train2014.zip

Archive:  train2014.zip
   creating: train2014/
 extracting: train2014/COCO_train2014_000000270070.jpg  
 extracting: train2014/COCO_train2014_000000101772.jpg  
 extracting: train2014/COCO_train2014_000000359320.jpg  
 extracting: train2014/COCO_train2014_000000486482.jpg  
 extracting: train2014/COCO_train2014_000000116155.jpg  
 extracting: train2014/COCO_train2014_000000082143.jpg  
 extracting: train2014/COCO_train2014_000000242307.jpg  
 extracting: train2014/COCO_train2014_000000510484.jpg  
 extracting: train2014/COCO_train2014_000000339597.jpg  
 extracting: train2014/COCO_train2014_000000366396.jpg  
 extracting: train2014/COCO_train2014_000000363942.jpg  
 extracting: train2014/COCO_train2014_000000244928.jpg  
 extracting: train2014/COCO_train2014_000000239417.jpg  
 extracting: train2014/COCO_train2014_000000045059.jpg  
 extracting: train2014/COCO_train2014_000000556018.jpg  
 extracting: train2014/COCO_train2014_000000328391.jpg  
 extracting: train2014/COCO_train2014_00

In [0]:
!wget https://s3.amazonaws.com/cvmlp/vqa/mscoco/vqa/Questions_Train_mscoco.zip

--2019-06-09 20:03:34--  https://s3.amazonaws.com/cvmlp/vqa/mscoco/vqa/Questions_Train_mscoco.zip
Resolving s3.amazonaws.com (s3.amazonaws.com)... 52.216.8.93
Connecting to s3.amazonaws.com (s3.amazonaws.com)|52.216.8.93|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 21985607 (21M) [application/zip]
Saving to: ‘Questions_Train_mscoco.zip’

Questions_Train_msc 100%[===================>]  20.97M  19.1MB/s    in 1.1s    

2019-06-09 20:03:35 (19.1 MB/s) - ‘Questions_Train_mscoco.zip’ saved [21985607/21985607]



In [0]:
!unzip Questions_Train_mscoco.zip

Archive:  Questions_Train_mscoco.zip
  inflating: OpenEnded_mscoco_train2014_questions.json  
  inflating: MultipleChoice_mscoco_train2014_questions.json  


In [0]:
!wget https://s3.amazonaws.com/cvmlp/vqa/mscoco/vqa/Annotations_Train_mscoco.zip

--2019-06-09 20:04:04--  https://s3.amazonaws.com/cvmlp/vqa/mscoco/vqa/Annotations_Train_mscoco.zip
Resolving s3.amazonaws.com (s3.amazonaws.com)... 52.216.10.77
Connecting to s3.amazonaws.com (s3.amazonaws.com)|52.216.10.77|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 12167843 (12M) [application/zip]
Saving to: ‘Annotations_Train_mscoco.zip’

Annotations_Train_m 100%[===================>]  11.60M  13.4MB/s    in 0.9s    

2019-06-09 20:04:05 (13.4 MB/s) - ‘Annotations_Train_mscoco.zip’ saved [12167843/12167843]



In [0]:
!unzip Annotations_Train_mscoco.zip


Archive:  Annotations_Train_mscoco.zip
  inflating: mscoco_train2014_annotations.json  


In [0]:
print(len(answer_vector))
print(len(image_name_vector))
print(len(questions_vector))
print(image_name_vector[:2])

209706
209706
209706
['train2014/COCO_train2014_000000487025.jpg', 'train2014/COCO_train2014_000000487025.jpg']


In [0]:
from vqa import VQA
import nltk
import os
from matplotlib import pyplot as plt
import pandas as pd
import numpy as np
nltk.download('punkt')

def text_processing(questions_file,answers_file,data_type):
  train_answer_file = "mscoco_train2014_annotations.json"
  train_question_file = "OpenEnded_mscoco_train2014_questions.json"
  vqa = VQA(train_answer_file, train_question_file)
  vqa.filter_by_ques_len(30)
  vqa.filter_by_ans_len(10)
  
  
  
  question_ids = list(vqa.qa.keys())
  image_ids = [vqa.qa[k]['image_id'] for k in question_ids]
  image_files = [os.path.join("train2014", "COCO_"+data_type+"_000000"+("%06d" %k)+".jpg")
                   for k in image_ids]
  questions = [vqa.qqa[k]['question'] for k in question_ids]
  answers = [vqa.qa[k]['best_answer'] for k in question_ids]
  
  
  
  annotations = pd.DataFrame({'question_id': question_ids,
                                'image_id': image_ids,
                                'image_file': image_files,
                                'question': questions,
                                'answer': answers})
  annotations.to_csv("my_annotation_file")
  
  
  
  all_captions = []
  for annot in annotations["question"]:
    capt = "<start> " + annot + " <end>"
    all_captions.append(capt)
    
  
#   all_answers = []
#   for answer in annotations["answer"]:
#     ans = "<start> " + answer + " <end>"
#     all_answers.append(ans)

  top_k = 5000
  tokenizer = tf.keras.preprocessing.text.Tokenizer(num_words=top_k, 
                                                  oov_token="<unk>", 
                                                  filters='!"#$%&()*+.,-/:;=?@[\]^_`{|}~ ')
  
  tokenizer.fit_on_texts(all_captions)
  tokenizer.word_index['<pad>'] = 0
  train_seqs = tokenizer.texts_to_sequences(all_captions)
  questions_vector = tf.keras.preprocessing.sequence.pad_sequences(train_seqs, padding='post')
  
  
#   answer_vector = tokenizer.texts_to_sequences(all_answers)
#   answer_vector=tf.keras.preprocessing.sequence.pad_sequences(answer_vector, padding='post')
  
  
  questions_vector = np.array(questions_vector)
  answers = np.array(answers)
  image_name_vector = list(annotations["image_file"])

  print(len(answers))
  print(len(image_name_vector))
  print(len(questions_vector))
  print(image_name_vector[:2])
  
  return tokenizer,image_name_vector,questions_vector,answers
  
tokenizer,image_name_vector,questions_vector,answer_vector = text_processing("mscoco_train2014_annotations.json",
                                                                            "OpenEnded_mscoco_train2014_questions.json",
                                                                            "train2014")


  

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
loading VQA annotations and questions into memory...
0:00:04.460456
creating index...


  0%|          | 1113/248349 [00:00<00:22, 11123.70it/s]

index created!
Filtering the questions by length...


100%|██████████| 248349/248349 [00:22<00:00, 11171.82it/s]


creating index...


  1%|          | 1364/248349 [00:00<00:18, 13633.84it/s]

index created!
Filtering the answers by length...


100%|██████████| 248349/248349 [00:17<00:00, 14045.70it/s]


creating index...
index created!
209706
209706
209706
['train2014/COCO_train2014_000000487025.jpg', 'train2014/COCO_train2014_000000487025.jpg']


In [0]:
tokenizer.sequences_to_texts(questions_vector[:10])

['<start> is there a shadow <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> is this one bench or multiple benches <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> is this a modern train <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> what color is the stripe on the train <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> what is on the other side of the train <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> is the bus driver on any kind of <unk> <unk> <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> is the bus moving <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> wha

In [0]:
sample_ans_long = [i for i,arr in enumerate(answer_vector) if len(arr) >3 ]
print(sample_ans_long[1])
tokenizer.sequences_to_texts(answer_vector[sample_ans_long[:10]])

1


['<start> yes <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> 1 <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> no <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> white <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> trees <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> no <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> yes <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> red <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> yes <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>',
 '<start> vegetables <end> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>']

In [61]:
tokenizer.word_index

{'<unk>': 1,
 '<start>': 2,
 '<end>': 3,
 'the': 4,
 'is': 5,
 'what': 6,
 'are': 7,
 'this': 8,
 'in': 9,
 'a': 10,
 'on': 11,
 'of': 12,
 'how': 13,
 'color': 14,
 'many': 15,
 'there': 16,
 'does': 17,
 'man': 18,
 'people': 19,
 'picture': 20,
 'to': 21,
 'wearing': 22,
 'it': 23,
 'these': 24,
 'or': 25,
 'have': 26,
 'person': 27,
 'photo': 28,
 'do': 29,
 'you': 30,
 'animal': 31,
 'kind': 32,
 'room': 33,
 'woman': 34,
 'they': 35,
 'be': 36,
 'animals': 37,
 'doing': 38,
 'holding': 39,
 'type': 40,
 'can': 41,
 'any': 42,
 'dog': 43,
 'for': 44,
 'at': 45,
 'he': 46,
 'train': 47,
 'that': 48,
 'cat': 49,
 'his': 50,
 'water': 51,
 'an': 52,
 'shirt': 53,
 'sign': 54,
 'where': 55,
 'see': 56,
 'bus': 57,
 'food': 58,
 'playing': 59,
 'sport': 60,
 'made': 61,
 'which': 62,
 'sitting': 63,
 "man's": 64,
 'plate': 65,
 'plane': 66,
 'table': 67,
 'with': 68,
 'shown': 69,
 'right': 70,
 'number': 71,
 'look': 72,
 'taken': 73,
 'left': 74,
 'all': 75,
 'being': 76,
 'white': 7

# Image preprocessing 

In [0]:
from sklearn.model_selection import train_test_split

In [0]:
def load_image(image_path,cap,answer_vector):
    img = tf.io.read_file(image_path)
    img = tf.image.decode_jpeg(img, channels=3)
    img = tf.image.resize(img, (299, 299))
    img = tf.keras.applications.inception_v3.preprocess_input(img)
    img = tf.expand_dims(img,0)
    img = image_features_extract_model(img)
    img = tf.reshape(img, (-1, img.shape[3]))
    return img,cap,answer_vector


In [0]:
image_model = tf.keras.applications.InceptionV3(include_top=False, 
                                                weights='imagenet')
new_input = image_model.input
hidden_layer = image_model.layers[-1].output

image_features_extract_model = tf.keras.Model(new_input, hidden_layer)


87916544/87910968 [==============================] - 3s 0us/step


In [0]:
BATCH_SIZE = 64
BUFFER_SIZE = 1000
embedding_dim = 256
units = 512
vocab_size = len(tokenizer.word_index)
# shape of the vector extracted from InceptionV3 is (64, 2048)
# these two variables represent that
features_shape = 2048
attention_features_shape = 64

In [0]:
dataset = tf.data.Dataset.from_tensor_slices((image_name_vector, questions_vector,answer_vector))

# using map to load the numpy files in parallel
# NOTE: Be sure to set num_parallel_calls to the number of CPU cores you have
# https://www.tensorflow.org/api_docs/python/tf/py_func
#dataset = dataset.map(lambda item1, item2,item3: tf.py_function(load_image, [item1, item2,item3], [tf.string, tf.int32,tf.int32]), num_parallel_calls=1)
dataset  =dataset.map(load_image)
# shuffling and batching
dataset = dataset.shuffle(BUFFER_SIZE)
# https://www.tensorflow.org/api_docs/python/tf/contrib/data/batch_and_drop_remainder
dataset = dataset.batch(BATCH_SIZE)
dataset = dataset.prefetch(1)

In [0]:
for dat in dataset.take(1):
  print(dat)

KeyboardInterrupt: ignored

In [0]:
def gru(units):
  # If you have a GPU, we recommend using the CuDNNGRU layer (it provides a 
  # significant speedup).
  if tf.test.is_gpu_available():
    return tf.keras.layers.CuDNNGRU(units, 
                                    return_sequences=True, 
                                    return_state=True, 
                                    recurrent_initializer='glorot_uniform')
  else:
    return tf.keras.layers.GRU(units, 
                               return_sequences=True, 
                               return_state=True, 
                               recurrent_activation='sigmoid', 
                               recurrent_initializer='glorot_uniform')

In [0]:
class BahdanauAttention(tf.keras.Model):
  def __init__(self, units):
    super(BahdanauAttention, self).__init__()
    self.W1 = tf.keras.layers.Dense(units)
    self.W2 = tf.keras.layers.Dense(units)
    self.V = tf.keras.layers.Dense(1)
  
  def call(self, features, hidden):
    # features(CNN_encoder output) shape == (batch_size, 64, embedding_dim)
    
    # hidden shape == (batch_size, hidden_size)
    # hidden_with_time_axis shape == (batch_size, 1, hidden_size)
    hidden_with_time_axis = tf.expand_dims(hidden, 1)
    
    # score shape == (batch_size, 64, hidden_size)
    score = tf.nn.tanh(self.W1(tf.cast(features,dtype=tf.float32)) + self.W2(tf.cast(hidden_with_time_axis,dtype=tf.float32)))
    
    # attention_weights shape == (batch_size, 64, 1)
    # we get 1 at the last axis because we are applying score to self.V
    attention_weights = tf.nn.softmax(self.V(score), axis=1)
    
    # context_vector shape after sum == (batch_size, hidden_size)
    context_vector = tf.cast(attention_weights,dtype=tf.float32) * tf.cast(features,dtype=tf.float32)
    context_vector = tf.reduce_sum(context_vector, axis=1)
    
    return context_vector, attention_weights

In [0]:
class CNN_Encoder(tf.keras.Model):
    # Since we have already extracted the features and dumped it using pickle
    # This encoder passes those features through a Fully connected layer
    def __init__(self, embedding_dim):
        super(CNN_Encoder, self).__init__()
        # shape after fc == (batch_size, 64, embedding_dim)
        self.fc = tf.keras.layers.Dense(embedding_dim)
        
    def call(self, x):
        x = self.fc(x)
        x = tf.nn.relu(x)
        return x

In [0]:
class RNN_Decoder_1(tf.keras.Model):
  def __init__(self, embedding_dim, units, vocab_size):
    super(RNN_Decoder_1, self).__init__()
    self.units = units

    self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim)
    self.gru = gru(self.units)
    self.fc1 = tf.keras.layers.Dense(self.units)
    self.fc2 = tf.keras.layers.Dense(vocab_size)
    
    self.attention = BahdanauAttention(self.units)
        
  def call(self, x, features, hidden):
    # defining attention as a separate model
    context_vector, attention_weights = self.attention(features, hidden)
    
    # x shape after passing through embedding == (batch_size, 1, embedding_dim)
    x = self.embedding(x)
    
    # x shape after concatenation == (batch_size, 1, embedding_dim + hidden_size)
    x = tf.concat([tf.expand_dims(context_vector, 1), x], axis=-1)
    #x = tf.concat([context_vector, x], axis=-1)
    
    # passing the concatenated vector to the GRU
    output, state = self.gru(x)
    
    # shape == (batch_size, max_length, hidden_size)
    x = self.fc1(output)
    
    #x shape == (batch_size * max_length, hidden_size)
    x = tf.reshape(x, (-1, x.shape[2]))
    
#     #output shape == (batch_size * max_length, vocab)
    x = self.fc2(x)

    return x, state, attention_weights

  def reset_state(self, batch_size):
    return tf.zeros((batch_size, self.units))
  
#   def train_step(self,img_tensor,annotations,answers,dec_input,features,hidden):
#     with tf.GradientTape() as tape:
#       features = encoder(img_tensor)
#       loss = 0
#       annots_list = []
      
#       annots_features = np.array((BATCH_SIZE,1,self.units))
#        #Decoder for the annotations
#       for i in range(1, annotations.shape[1]):
#                       # passing the features through the decoder
#         annots, hidden, _ = self.call(dec_input, features, hidden)

#         #loss += loss_function(annotations[:, i], annots)

#         annots_features= np.vstack(annots_features,annots)

        

#          # using teacher forcing
#         dec_input = tf.expand_dims(annotations[:, i], 1)
      
#       #Decoder for the answers 
#       ans_input = tf.expand_dims([tokenizer.word_index['<start>']] * BATCH_SIZE, 1)
#       for i in range(1,answers.shape[1]):
        
#         ans,hidden,_ = self.call(ans_input,annots_list[i],hidden)
     
        
#         # x shape == (batch_size * max_length, hidden_size)
#         ans = tf.reshape(ans, (-1, ans.shape[2]))

#         # output shape == (batch_size * max_length, vocab)
#         ans = self.fc2(ans)
        
           
#         loss += loss_function(answers[:, i], ans)
#         ans_input = tf.expand_dims(answers[:, i], 1)

      
#       self.train_loss(loss)
#       variables = encoder.variables + self.variables

#       gradients = tape.gradient(loss, variables) 

#       optimizer.apply_gradients(zip(gradients, variables), tf.train.get_or_create_global_step())
  
#   def train(self,dataset,num_epochs):
    
#     self.train_loss = tf.keras.metrics.Mean(name='train_loss')
#     self.eval_loss = tf.keras.metrics.Mean(name='eval_loss')
    
#     for epoch in range(EPOCHS):
#       start = time.time()
#       total_loss = 0
#       start_time = time.time()
#       self.train_loss.reset_states()
#       self.eval_loss.reset_states()

#       for (batch, (img_tensor,annotation, answer)) in enumerate(dataset):
          

#           # initializing the hidden state for each batch
#           # because the captions are not related from image to image
#           hidden = self.reset_state(batch_size=target.shape[0])

#           dec_input = tf.expand_dims([tokenizer.word_index['<start>']] * BATCH_SIZE, 1)
# #           predictions_list = numpy.zeros
          
#           self.train_step(img_tensor,annotations,answers,dec_input,features,hidden)
      
#           print('Epoch: {0}, Time: {1:.2f}, Train Loss: {2:.2f}'.format(epoch + 1,time.time() - start_time,
#                                                                                               self.train_loss.result()))



# #           total_loss += (loss / int(target.shape[1]))

          
# #           if batch % 100 == 0:
# #               print ('Epoch {} Batch {} Loss {:.4f}'.format(epoch + 1, 
# #                                                             batch, 
# #                                                             loss.numpy() / int(target.shape[1])))
#       # storing the epoch end loss value to plot later
# #       loss_plot.append(total_loss / len(questions_vector))

# #       print ('Epoch {} Loss {:.6f}'.format(epoch + 1, 
# #                                            total_loss/len(questions_vector)))
# #       print ('Time taken for 1 epoch {} sec\n'.format(time.time() - start))
    

In [0]:
class RNN_Decoder_2(tf.keras.Model):
  def __init__(self, embedding_dim, units, vocab_size):
    super(RNN_Decoder_2, self).__init__()
    self.units = units

    self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim)
    self.gru = gru(self.units)
    self.fc1 = tf.keras.layers.Dense(self.units)
    self.fc2 = tf.keras.layers.Dense(vocab_size)
    
    self.attention = BahdanauAttention(self.units)
        
  def call(self, x, features, hidden):
    # defining attention as a separate model
    context_vector, attention_weights = self.attention(features, hidden)
    
    # x shape after passing through embedding == (batch_size, 1, embedding_dim)
    x = self.embedding(x)
    
    # x shape after concatenation == (batch_size, 1, embedding_dim + hidden_size)
    #x = tf.concat([tf.expand_dims(context_vector, 1), x], axis=-1)
    x = tf.concat([context_vector, x], axis=-1)
    
    # passing the concatenated vector to the GRU
    output, state = self.gru(x)
    
    # shape == (batch_size, max_length, hidden_size)
    x = self.fc1(output)
    
    #x shape == (batch_size * max_length, hidden_size)
    x = tf.reshape(x, (-1, x.shape[2]))
    
    #output shape == (batch_size * max_length, vocab)
    x = self.fc2(x)

    return x, state, attention_weights

  def reset_state(self, batch_size):
    return tf.zeros((batch_size, self.units))

In [0]:
encoder = CNN_Encoder(embedding_dim)
decoder_1 = RNN_Decoder_1(embedding_dim, units, vocab_size)
decoder_2 = RNN_Decoder_2(embedding_dim, units, vocab_size)



In [0]:
import datetime
train_loss = tf.keras.metrics.Mean(name='train_loss')
eval_loss = tf.keras.metrics.Mean(name='eval_loss')
train_accuracy = tf.keras.metrics.SparseCategoricalAccuracy('train_accuracy')
eval_accuracy =  tf.keras.metrics.SparseCategoricalAccuracy('eval_accuracy')

current_time = datetime.datetime.now().strftime("%Y%m%d-%H%M%S")
train_log_dir = 'logs/gradient_tape/' + current_time + '/train'
test_log_dir = 'logs/gradient_tape/' + current_time + '/test'
train_summary_writer = tf.summary.create_file_writer(train_log_dir)
test_summary_writer = tf.summary.create_file_writer(test_log_dir)



In [0]:
def train_step_out(img_tensor,annotations,answers,dec_input,hidden):
    with tf.GradientTape() as tape:
      features = encoder(img_tensor)
      loss = 0
      
      
      annots_features = np.empty((BATCH_SIZE,1,units))
      
      
      
       #Decoder for the annotations
      for i in range(1, annotations.shape[1]):
                      # passing the features through the decoder
        annots, hidden, _ = decoder_1(dec_input, features, hidden)
        annots = tf.reshape(annots, (BATCH_SIZE, 1,-1))
       
        # using teacher forcing
        dec_input = tf.expand_dims(annotations[:, i], 1)
        
        #print(tf.shape(annots))
        #annots_features= np.concatenate((annots_features,annots),axis=1)
        #loss += loss_function(predictions[:, i], annots)

        

      
     
      
      #Decoder for the answers 
#       ans_input = tf.expand_dims([tokenizer.word_index['<start>']] * BATCH_SIZE, 1)
#       for i in range(1,answers.shape[1]):
#         print(tf.shape(ans_input),tf.shape(annots_features),tf.shape(hidden))
#         ans,hidden,_ = decoder_2(ans_input,annots_features,hidden)
     
        
        # x shape == (batch_size * max_length, hidden_size)
#         ans = tf.reshape(ans, (-1, ans.shape[2]))

#         # output shape == (batch_size * max_length, vocab)
#         ans = tf.keras.layers.Dense(vocab_size)(ans)
        
           
#         loss += loss_function(answers[:, i], ans)
#         accuracy += train_accuracy(answers[:, i], ans)
#         ans_input = tf.expand_dims(answers[:, i], 1)

      predictions = tf.keras.layers.Dense(vocab_size)(hidden)
      train_loss(predictions,answers)
      train_accuracy(predictions,answers)
      variables = encoder.variables + decoder_1.variables +decoder_2.variables

      gradients = tape.gradient(loss, variables) 

      optimizer.apply_gradients(zip(gradients, variables), tf.train.get_or_create_global_step())
      
      

In [0]:
def train_out(dataset,num_epochs):
    
    
    for epoch in range(num_epochs):
      start = time.time()
      total_loss = 0
      start_time = time.time()
      train_loss.reset_states()
      eval_loss.reset_states()

      for (batch, (img_tensor,annotation, answer)) in enumerate(dataset):
          
          print(batch)
          # initializing the hidden state for each batch
          # because the captions are not related from image to image
          hidden = decoder_1.reset_state(batch_size=annotation.shape[0])

          dec_input = tf.expand_dims([tokenizer.word_index['<start>']] * BATCH_SIZE, 1)
#           predictions_list = numpy.zeros
          
          train_step_out(img_tensor,annotation,answer,dec_input,hidden)
          with train_summary_writer.as_default():
            tf.summary.scalar('loss', train_loss.result(), step=epoch)
            tf.summary.scalar('accuracy', train_accuracy.result(), step=epoch)
      
          print('Epoch: {0}, Time: {1:.2f}, Train Loss: {2:.2f}'.format(epoch + 1,time.time() - start_time,
                                                                                              train_loss.result()))

In [0]:
!rm -rf ./logs/ 

In [0]:
train_out(dataset,2)

In [0]:
for img_tensor,annotation, answer in dataset.take(1):
  print(tf.shape(img_tensor),tf.shape(annotation), tf.shape(answer))

In [0]:
EPOCHS = 20

for epoch in range(EPOCHS):
    start = time.time()
    total_loss = 0
    
    for (batch, (img_tensor,annotation, answer)) in enumerate(dataset):
        loss = 0
        
        # initializing the hidden state for each batch
        # because the captions are not related from image to image
        hidden = decoder.reset_state(batch_size=target.shape[0])

        dec_input = tf.expand_dims([tokenizer.word_index['<start>']] * BATCH_SIZE, 1)
        predictions_list = numpy.zeros
        
        with tf.GradientTape() as tape:
            features = encoder(img_tensor)
            
            for i in range(1, target.shape[1]):
                # passing the features through the decoder
                predictions, hidden, _ = decoder(dec_input, features, hidden)

                loss += loss_function(target[:, i], predictions)
                
                predictions_list.append(predictions)
                
                
                
                # using teacher forcing
                dec_input = tf.expand_dims(target[:, i], 1)
            
            
        
        total_loss += (loss / int(target.shape[1]))
        
        variables = encoder.variables + decoder.variables
        
        gradients = tape.gradient(loss, variables) 
        
        optimizer.apply_gradients(zip(gradients, variables), tf.train.get_or_create_global_step())
        
        if batch % 100 == 0:
            print ('Epoch {} Batch {} Loss {:.4f}'.format(epoch + 1, 
                                                          batch, 
                                                          loss.numpy() / int(target.shape[1])))
    # storing the epoch end loss value to plot later
    loss_plot.append(total_loss / len(questions_vector))
    
    print ('Epoch {} Loss {:.6f}'.format(epoch + 1, 
                                         total_loss/len(questions_vector)))
    print ('Time taken for 1 epoch {} sec\n'.format(time.time() - start))

KeyboardInterrupt: ignored

In [0]:
for dat in dataset.take(1):
  print(dat)

NameError: ignored

In [0]:
!tensorboard --logdir logs/gradient_tape


TensorBoard 1.14.0a20190301 at http://99ef1ef4e292:6006 (Press CTRL+C to quit)
^C


In [0]:
!git init


Initialized empty Git repository in /content/.git/


In [0]:
!git status


On branch master

No commits yet

Untracked files:
  (use "git add <file>..." to include in what will be committed)

	.config/
	sample_data/

nothing added to commit but untracked files present (use "git add" to track)


In [0]:
git add 